In [1]:
# Librerias 
import pandas as pd
import folium
from geopy.distance import geodesic
import sys
import branca.colormap as cm
import numpy as np
import plotly.express as px

sys.path.append('../scripts')
from tipos_comercios import diccionario_categorias
from Eliminar_duplicados_geográficos import eliminar_duplicados_geograficos, mapa_por_categoria

In [2]:

# ------------------------------
# 1. Cargar diccionario SCIAN
# ------------------------------

# Se carga el archivo Excel con el diccionario del SCIAN, que contiene los códigos y títulos de actividades económicas
scian = pd.read_excel(
    "C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/MacroDatos/Diccionarios/Diccionario SCIAN.xlsx"
)

# Se filtran solo los registros que tienen un código de exactamente 3 dígitos (SCIAN a nivel agregación de 3 dígitos)
# Luego se elimina cualquier carácter "T" al final del título y se seleccionan únicamente las columnas relevantes
scian = (
    scian[scian["Código"].astype(str).str.fullmatch(r"^\d{3}")]
    .assign(Título=lambda x: x["Título"].str.rstrip("T"))
    [["Código", "Título"]]
)

# ------------------------------
# 2. Cargar datos del DENUE de Baja California
# ------------------------------

# Se cargan los datos de establecimientos económicos en Baja California
# Se usa codificación 'latin1' para evitar errores por caracteres especiales
df_baja_california = pd.read_csv("../data/Tijuana_comercios.csv", encoding="latin1")

# Se seleccionan únicamente las columnas relevantes para el análisis
df_baja_california = df_baja_california[
    ['entidad', 'municipio', 'nom_estab', 'codigo_act', 'nombre_act',
     'per_ocu', 'tipoCenCom', 'latitud', 'longitud']
].copy()

# ------------------------------
# 3. Preparar código SCIAN para unión
# ------------------------------

# Se extraen los primeros tres dígitos del código de actividad económica
# para hacer coincidir con el nivel de 3 dígitos del SCIAN
df_baja_california["codigo_act"] = df_baja_california["codigo_act"].astype(str).str[:3]

# ------------------------------
# 4. Unir SCIAN con DENUE
# ------------------------------

# Se realiza una unión (merge) entre la base del DENUE y el diccionario SCIAN
# usando el código de 3 dígitos como clave de unión
df_baja_california = df_baja_california.merge(
    scian, left_on="codigo_act", right_on="Código", how="left"
)

# ------------------------------
# 5. Renombrar y reorganizar columna de actividad principal
# ------------------------------

# Se renombra la columna 'Título' como 'Principal Actividad Economica'
df_baja_california = df_baja_california.rename(
    columns={"Título": "Principal Actividad Economica"}
)

# Se reposiciona la nueva columna para que esté más accesible visualmente (posición 5)
col_actividad = df_baja_california.pop("Principal Actividad Economica")
df_baja_california.insert(5, "Principal Actividad Economica", col_actividad)

# ------------------------------
# 6. Cargar datos adicionales
# ------------------------------

# Se cargan coordenadas de restaurantes de la competencia
datos_competencia = pd.read_csv("../data/Coordenadas_restaurantes_competencia.csv")

# Se cargan coordenadas de sucursales de Cabanna
datos_sucursales = pd.read_csv("../data/Datos_restaurantes_Cabanna.csv")

# Mostrar el DataFrame final de sucursales (útil en notebooks para ver los datos)
datos_sucursales

id_sucursal          nombre_sucursal            ciudad  \
0      CAB002                  Tijuana           Tijuana   
1      CAB009            Ciudad Juárez     Ciudad Juárez   
2      CAB007             Metropolitan         Monterrey   
3      CAB001                 Culiacán          Culiacán   
4      CAB003                 Mexicali          Mexicali   
5      CAB006                  Polanco  Ciudad de México   
6      CAB004    Guadalajara Av México       Guadalajara   
7      CAB008                   Puebla            Puebla   
8      CAB005  Guadalajara Gpurmeteria       Guadalajara   

                                           direccion    latitud    longitud  \
0  Plaza Paseo Chapultepec. Blvd. Agua Caliente N...  32.513932 -117.012145   
1  Blvd. Tomás Fernández 7533 Col. Partido Doblad...  31.732768 -106.412526   
2  Metropolitan Center. Av. Lázaro Cárdenas Nº 24...  25.650407 -100.333428   
3  Torre 3 Ríos. Blvd. Francisco Labastida Ochoa ...  24.815849 -107.399893   
4  Plaza La Gran Vía. Calzada Cetys Nº 1950 Col. ...  32.653485 -115.410284   
5  Av. Presidente Mazaryk Nº 134, Col. Polanco. D...  19.431454  -99.186981   
6               Av. México Nº 2972, Col. Residencial  20.679919 -103.390796   
7  Centro Comercial Solesta. Atlixcáyotl Nº 4931 ...  19.034475  -98.227831   
8  Plaza La Gourmeteria. Av. López Mateos Sur Nº ...  20.586672 -103.447072   

   ventas_totales  clientes_totales  
0          794493            170038  
1          776782            141858  
2          706797            130300  
3          689705            177865  
4          681583            145303  
5          498685             81623  
6          497524             89270  
7          368657             70295  
8          254960             45860

---

### Análisis descriptivo

> Lo primero será generar indicadores y comparaciones simples, pero útiles para comprender el contexto general de los datos.

- Identificaremos patrones iniciales relevantes.
- Compararemos categorías de interés.




In [ ]:

ventas = datos_sucursales["ventas_totales"].sum()
clientes = datos_sucursales["clientes_totales"].sum()

print(f"Ventas totales: {ventas:,}")
print(f"Clientes totales: {clientes:,}")

Ventas totales: 5,269,186
Clientes totales: 1,052,412


In [4]:
# ==========================================
# Análisis de desempeño por sucursal Cabanna
# ==========================================

# ------------------------------
# 1. Calcular ventas promedio por cliente
# ------------------------------

# Se crea una nueva columna 'ventas_por_cliente' dividiendo el total de ventas entre el total de clientes
# Esto da una idea del ticket promedio por cliente en cada sucursal
datos_sucursales["ventas_por_cliente"] = (
    datos_sucursales["ventas_totales"] / datos_sucursales["clientes_totales"]
)

# ------------------------------
# 2. Ordenar sucursales por métricas clave
# ------------------------------

# Ordena las sucursales de mayor a menor según las ventas totales
top_ventas = datos_sucursales.sort_values("ventas_totales", ascending=False)

# Ordena las sucursales de mayor a menor según la cantidad de clientes totales
top_clientes = datos_sucursales.sort_values("clientes_totales", ascending=False)

# ------------------------------
# 3. Mostrar el top 10 de sucursales con mayores ventas
# ------------------------------

# Se muestran las 10 sucursales con más ventas junto con su nombre y monto total vendido
top_ventas[["nombre_sucursal", "ventas_totales"]]


nombre_sucursal  ventas_totales
0                  Tijuana          794493
1            Ciudad Juárez          776782
2             Metropolitan          706797
3                 Culiacán          689705
4                 Mexicali          681583
5                  Polanco          498685
6    Guadalajara Av México          497524
7                   Puebla          368657
8  Guadalajara Gpurmeteria          254960

In [5]:
# ------------------------------
# 4. Mostrar el top 10 de sucursales con mayores clientes
# ------------------------------

# Se muestran las 10 sucursales con más clientes junto con su nombre y monto total vendido
top_clientes[["nombre_sucursal", "clientes_totales"]].head(10)

nombre_sucursal  clientes_totales
3                 Culiacán            177865
0                  Tijuana            170038
4                 Mexicali            145303
1            Ciudad Juárez            141858
2             Metropolitan            130300
6    Guadalajara Av México             89270
5                  Polanco             81623
7                   Puebla             70295
8  Guadalajara Gpurmeteria             45860

In [6]:
# ------------------------------
# 5. Mostrar el top 10 de sucursales con mayores ventas por cliente
# ------------------------------

# Se muestran las 10 sucursales con más ventas por cliente junto con su nombre y monto total vendido

top_vpc = datos_sucursales.sort_values("ventas_por_cliente", ascending=False)
top_vpc[["nombre_sucursal", "ventas_por_cliente"]].head(10)


nombre_sucursal  ventas_por_cliente
5                  Polanco            6.109614
6    Guadalajara Av México            5.573250
8  Guadalajara Gpurmeteria            5.559529
1            Ciudad Juárez            5.475772
2             Metropolitan            5.424382
7                   Puebla            5.244427
4                 Mexicali            4.690770
0                  Tijuana            4.672444
3                 Culiacán            3.877688

In [7]:
# ==========================================
# Mapa de sucursales Cabanna por ventas totales
# ==========================================

# ------------------------------
# 1. Calcular centro del mapa
# ------------------------------

# Calculamos la ubicación promedio (latitud y longitud) de todas las sucursales
# Esto servirá como punto central para inicializar el mapa
centro_mapa = [
    datos_sucursales["latitud"].mean(),
    datos_sucursales["longitud"].mean()
]

# Creamos el mapa base con un nivel de zoom adecuado para cubrir múltiples estados
mapa_sucursales = folium.Map(location=centro_mapa, zoom_start=6)

# ------------------------------
# 2. Crear un colormap para representar las ventas
# ------------------------------

# El colormap asigna colores según el valor de las ventas totales por sucursal
# Verde = ventas bajas, Naranja = medias, Rojo = altas
colormap = cm.LinearColormap(
    colors=["green", "orange", "red"],
    vmin=datos_sucursales["ventas_totales"].min(),
    vmax=datos_sucursales["ventas_totales"].max(),
)
colormap.caption = "Ventas totales por sucursal (MXN)"
colormap.add_to(mapa_sucursales)

# ------------------------------
# 3. Añadir sucursales al mapa
# ------------------------------

# Recorremos cada sucursal para agregarla como un marcador circular al mapa
for _, row in datos_sucursales.iterrows():
    # Color de acuerdo con las ventas
    color = colormap(row["ventas_totales"])

    # Se crea un círculo en la ubicación de la sucursal con un tooltip informativo
    folium.CircleMarker(
        location=[row["latitud"], row["longitud"]],
        radius=10,  # tamaño fijo de los círculos
        color=color,  # borde del círculo
        fill=True,
        fill_opacity=0.8,
        tooltip=f"""
        <b>{row['nombre_sucursal']}</b><br>
        Ventas: ${row['ventas_totales']:,.0f}<br>
        Clientes: {row['clientes_totales']:,}
        """,
    ).add_to(mapa_sucursales)

# ------------------------------
# 4. Mostrar mapa interactivo
# ------------------------------

# Se visualiza el mapa interactivo en Jupyter Notebook
mapa_sucursales


---

### Análisis detallado: sucursal Cabanna Tijuana

Después de explorar el desempeño general de todas las sucursales, el siguiente paso será enfocarnos en **Cabanna Tijuana**.

Analizaremos su entorno competitivo, el perfil de negocios cercanos, y su rendimiento en comparación con otras ubicaciones. Esto nos permitirá entender:

- ¿Qué tan densa es la competencia en su zona?
- ¿Qué tipo de comercios predominan a su alrededor?
- ¿Cómo se comportan las ventas y el flujo de clientes en ese contexto?

Este enfoque territorial nos ayudará a identificar oportunidades y riesgos locales que podrían estar impactando su desempeño.


In [8]:
# ==============================
# Análisis geoespacial de competencia en Tijuana
# ==============================

# ------------------------------
# 1. Obtener coordenadas de la sucursal Cabanna en Tijuana
# ------------------------------

# Filtra el DataFrame de sucursales para encontrar la sucursal de Cabanna ubicada en Tijuana
# Se usa `.iloc[0]` porque se espera un solo resultado
sucursal_tijuana = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Tijuana"].iloc[0]

# Se extraen las coordenadas (latitud, longitud) de la sucursal
coord_cabanna = (sucursal_tijuana["latitud"], sucursal_tijuana["longitud"])

# ------------------------------
# 2. Calcular distancia geodésica desde cada comercio a Cabanna Tijuana
# ------------------------------

# Se calcula la distancia entre cada comercio en Baja California y la sucursal Cabanna en Tijuana
# Se usa geodesic (que toma en cuenta la curvatura de la tierra) para mayor precisión
df_baja_california["distancia_m"] = df_baja_california.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna).meters,
    axis=1
)

# Se ordenan los comercios por distancia ascendente (los más cercanos primero)
df_baja_california.sort_values(by="distancia_m", inplace=True)

# ------------------------------
# 3. Filtrar únicamente los comercios del municipio de Tijuana
# ------------------------------

df_tijuana = df_baja_california[df_baja_california['municipio'] == 'Tijuana'].copy()

# Se eliminan columnas que ya no se necesitan para el análisis final
df_tijuana.drop(columns=['Código', 'codigo_act'], inplace=True)

# ------------------------------
# 4. Filtrar comercios dentro de un radio de 500 metros de Cabanna
# ------------------------------

df_tijuana_filtrado_500 = df_tijuana[df_tijuana["distancia_m"] <= 500]

# ------------------------------
# 5. Eliminar duplicados geográficos (comercios muy cercanos con misma lat/lon)
# ------------------------------

# Se asume que `eliminar_duplicados_geograficos` es una función definida previamente
df_tijuana = eliminar_duplicados_geograficos(df_tijuana_filtrado_500)

# Se vuelve a ordenar por distancia tras eliminar duplicados
df_tijuana.sort_values(by="distancia_m", inplace=True)

# ------------------------------
# 6. Exportar resultado limpio a CSV
# ------------------------------

df_tijuana.to_csv("../data/denue_tijuana_data.csv", index=False)

# ------------------------------
# 7. Agrupar nombre de actividad económica por categorías simplificadas
# ------------------------------

# Reemplaza los nombres originales por categorías más agregadas usando un diccionario
# `diccionario_categorias` debe estar definido previamente como {'nombre original': 'categoría simple'}
df_tijuana["nombre_act"] = df_tijuana["nombre_act"].replace(diccionario_categorias)

# Mostrar los primeros 5 registros como vista previa
#df_tijuana.head(5)



### 1. Densidad de negocios por metro cuadrado

Tomando el buffer circular de **500 metros** alrededor de la sucursal, el área se calcula con la fórmula del área de un círculo:


$$A = \pi r^2 = \pi \times (500)^2 = 785{,}398 \ \text{m}^2$$


Este valor se usará como base para calcular la densidad de negocios por metro cuadrado.




In [9]:
# ==============================================
# Cálculo de densidad de competencia alrededor de Cabanna Tijuana
# ==============================================

# ------------------------------
# 1. Calcular el área del buffer circular de 500 metros
# ------------------------------

# Se utiliza la fórmula del área de un círculo: A = π * r²
# En este caso, r = 500 metros
area_m2 = np.pi * (500**2)  # Resultado ≈ 785,398 m²

# ------------------------------
# 2. Contar número de comercios dentro del buffer
# ------------------------------

# Se toma el número de filas del DataFrame filtrado (df_tijuana),
# que ya contiene solo los comercios dentro del radio de 500 m
num_comercios = df_tijuana.shape[0]

# ------------------------------
# 3. Calcular densidad de competencia (comercios por m²)
# ------------------------------

# Se divide el número de comercios entre el área del buffer
# El resultado es un valor de densidad: cuántos comercios hay por metro cuadrado
densidad_competencia = num_comercios / area_m2

# ------------------------------
# 4. Asignar el valor de densidad a la sucursal Tijuana
# ------------------------------

# Se guarda este valor en una nueva columna en el DataFrame `datos_sucursales`,
# específicamente para la fila correspondiente a la sucursal "Tijuana"
datos_sucursales.loc[
    datos_sucursales["nombre_sucursal"] == "Tijuana",
    "densidad_competencia_500m"
] = densidad_competencia

densidad_competencia

0.0007397521754911295


**Resultado de la densidad de negocios**

La **densidad de negocios** es de:

$$0.000739752 \ \text{comercios/m}^2$$

Lo que equivale aproximadamente a:

$$739.75 \ \text{comercios/km}^2$$

Este valor representa la **cantidad de negocios** dentro del radio de 500 metros (área de influencia inmediata) alrededor de la sucursal Cabanna Tijuana.


### 2 Conteo de comercios por categoría (Actividad)

Este análisis permite identificar si existe **saturación de algún giro comercial** dentro del área de influencia de la sucursal Cabanna Tijuana (500 metros).

Por ejemplo:
- ¿Hay una alta concentración de **cafés**?
- ¿Predominan los **restaurantes**?
- ¿Existen muchos **bares o cantinas**?

El objetivo es detectar patrones de concentración que puedan estar afectando la competitividad o diferenciación de la sucursal.



In [10]:
# ===============================================
# Conteo de comercios por categoría (nombre_act)
# ===============================================

# ------------------------------
# 1. Contar frecuencia de cada categoría
# ------------------------------

# Se cuenta cuántos comercios hay por categoría de actividad dentro del radio de 500m
# `nombre_act` contiene el giro comercial como "cafetería", "restaurante", "bar", etc.
conteo_por_categoria = df_tijuana["nombre_act"].value_counts().reset_index()

# Se renombran las columnas para mayor claridad
conteo_por_categoria.columns = ["categoria", "conteo"]

# ------------------------------
# 2. (Opcional) Exportar a CSV para usar en reportes externos
# ------------------------------

# Si se desea guardar el conteo para documentación o análisis adicional:
# conteo_por_categoria.to_csv("../data/conteo_categorias_500m_Tijuana.csv", index=False)

# ------------------------------
# 3. Mostrar resultados clave
# ------------------------------

# Mostrar el número total de comercios en el área de análisis
print("Número total de comercios en un radio de 500m de Cabanna:", conteo_por_categoria['conteo'].sum())

# Mostrar las 20 categorías más frecuentes
conteo_por_categoria.head(20)


Número total de comercios en un radio de 500m de Cabanna: 581


categoria  conteo
0                        Restaurantes      48
1                 Despachos jurídicos      34
2                  Salones de belleza      33
3               Cafeterías y neverías      30
4                              Bancos      25
5              Contadores y auditores      16
6               Consultorios dentales      15
7                       Inmobiliarias      13
8           Renta de oficinas/locales      11
9          Consultoría administrativa      10
10                   Bares y cantinas       9
11                 Centros cambiarios       9
12          Restaurantes autoservicio       8
13                 Agentes de seguros       8
14                       Call centers       8
15  Construcción vivienda unifamiliar       7
16                         Psicólogos       7
17              Taquerías y torterías       6
18                   Estacionamientos       6
19                        Nutriólogos       6

In [11]:

px.bar(
    conteo_por_categoria.head(10),
    x="conteo", y="categoria",
    orientation="h",
    title="Top 10 categorías comerciales en radio de 500m",
    labels={"conteo": "Número de comercios", "categoria": "Categoría"}
)




**Interpretación objetiva de la distribución comercio**

La zona de influencia inmediata (500 m a la redonda) de la sucursal **Cabanna Tijuana** cuenta con un total de **581 comercios**, incluyendo la propia sucursal. A continuación, se describe la composición comercial más representativa:

- **Restaurantes** son el giro con mayor presencia, con **48 establecimientos**, lo que representa aproximadamente **8.26 %** del total.
  
- El **segundo y tercer giro más común** corresponden a **despachos jurídicos** (34) y **salones de belleza** (33), reflejando una importante oferta de **servicios profesionales y personales**.

- Las **cafeterías y neverías**, con **30 unidades**, aportan una alternativa adicional en el segmento de **alimentos y bebidas**, distinta a los restaurantes tradicionales.

- **Bares y cantinas** (9) y **taquerías/torterías** (6) también figuran dentro de la oferta gastronómica, principalmente vinculada al **consumo informal y nocturno**.

- En conjunto, los giros directamente relacionados con **alimentos y bebidas** (restaurantes, cafeterías, bares, autoservicios y taquerías) suman **101 establecimientos**, lo que representa un **17.38 %** del total.

- Los **servicios financieros** (bancos, casas de cambio y agentes de seguros) alcanzan **42 unidades**, consolidándose como un bloque relevante en la zona.

- Se identificaron al menos **8 call centers** y **11 negocios de renta de oficinas o locales**, lo que sugiere una **presencia activa de servicios corporativos** y de apoyo al comercio formal.

- Finalmente, los **servicios de salud privada** también están representados, con **28 unidades** entre **consultorios dentales, psicólogos y nutriólogos**, lo cual indica una **oferta importante de atención médica personalizada**.





## Validación Visual: Mapa de Competencia Directa

Se presenta a continuación un **mapa interactivo generado con Folium**, que permite visualizar la **competencia directa** alrededor de la sucursal Cabanna Tijuana.

Este mapa muestra los comercios identificados dentro de un radio de **500 metros**, facilitando la validación visual de su ubicación, densidad y proximidad relativa a la sucursal.



In [12]:

# Filtrar competencia en Tijuana
competencia_tijuana = datos_competencia[datos_competencia["ciudad"] == "Tijuana"].copy()

import folium
from geopy.distance import geodesic

# Crear mapa centrado en Cabanna
mapa = folium.Map(location=coord_cabanna, zoom_start=17)

# Añadir punto de Cabanna
folium.Marker(
    coord_cabanna, 
    tooltip="Cabanna Tijuana", 
    icon=folium.Icon(color="red")
).add_to(mapa)

# Añadir buffer de 500 metros
folium.Circle(
    coord_cabanna, 
    radius=500, 
    color='blue', 
    fill=True, 
    fill_opacity=0.1
).add_to(mapa)



# Añadir competencia directa en verde y dibujar líneas con distancia
for _, row in competencia_tijuana.iterrows():
    coord_competidor = (row['latitud'], row['longitud'])
    distancia_m = geodesic(coord_cabanna, coord_competidor).meters
    etiqueta = f"{row['restaurante']} ({round(distancia_m,1)} m)"

    # Marcar competidor en verde
    folium.Marker(
        location=coord_competidor,
        tooltip=etiqueta,
        icon=folium.Icon(color="green", icon="cutlery", prefix="fa")
    ).add_to(mapa)

    # Dibujar línea
    folium.PolyLine(
        locations=[coord_cabanna, coord_competidor],
        color="green",
        weight=2,
        opacity=0.7
    ).add_to(mapa)

# Mostrar mapa
mapa


In [13]:

'''lat_cabanna = 32.5139321708603
lon_cabanna = -117.01214532032895

ponderaciones = {
    'mañana': {'laboral': 0.9, 'residencial': 0.3, 'comercial': 0.7, 'entretenimiento': 0.2},
    'tarde': {'laboral': 0.5, 'residencial': 0.6, 'comercial': 1.0, 'entretenimiento': 0.6},
    'noche': {'laboral': 0.3, 'residencial': 0.4, 'comercial': 0.7, 'entretenimiento': 1.0}
}


import folium
from folium.plugins import HeatMap

def crear_mapa_por_horario(df, horario, lat_cabanna, lon_cabanna):
    df['peso'] = df['tipo_zona'].apply(lambda x: ponderaciones[horario].get(x, 0))
    
    m = folium.Map(location=[lat_cabanna, lon_cabanna], zoom_start=14)
    
    # Agrega la sucursal Cabanna
    folium.Marker(
        [lat_cabanna, lon_cabanna], 
        popup='Cabanna Tijuana', 
        icon=folium.Icon(color='red')
    ).add_to(m)
    
    # Generar datos para el mapa de calor
    heat_data = [[row['latitud'], row['longitud'], row['peso']] for idx, row in df.iterrows()]
    
    HeatMap(heat_data, radius=25).add_to(m)
    
    return m

mapa_manana = crear_mapa_por_horario(competencia_tijuana.copy(), 'mañana', lat_cabanna, lon_cabanna)
mapa_manana.save("mapa_atraccion_manana.html")

mapa_tarde = crear_mapa_por_horario(competencia_tijuana.copy(), 'tarde', lat_cabanna, lon_cabanna)
mapa_tarde.save("mapa_atraccion_tarde.html")

mapa_noche = crear_mapa_por_horario(competencia_tijuana.copy(), 'noche', lat_cabanna, lon_cabanna)
mapa_noche.save("mapa_atraccion_noche.html")'''


'lat_cabanna = 32.5139321708603\nlon_cabanna = -117.01214532032895\n\nponderaciones = {\n    \'mañana\': {\'laboral\': 0.9, \'residencial\': 0.3, \'comercial\': 0.7, \'entretenimiento\': 0.2},\n    \'tarde\': {\'laboral\': 0.5, \'residencial\': 0.6, \'comercial\': 1.0, \'entretenimiento\': 0.6},\n    \'noche\': {\'laboral\': 0.3, \'residencial\': 0.4, \'comercial\': 0.7, \'entretenimiento\': 1.0}\n}\n\n\nimport folium\nfrom folium.plugins import HeatMap\n\ndef crear_mapa_por_horario(df, horario, lat_cabanna, lon_cabanna):\n    df[\'peso\'] = df[\'tipo_zona\'].apply(lambda x: ponderaciones[horario].get(x, 0))\n\n    m = folium.Map(location=[lat_cabanna, lon_cabanna], zoom_start=14)\n\n    # Agrega la sucursal Cabanna\n    folium.Marker(\n        [lat_cabanna, lon_cabanna], \n        popup=\'Cabanna Tijuana\', \n        icon=folium.Icon(color=\'red\')\n    ).add_to(m)\n\n    # Generar datos para el mapa de calor\n    heat_data = [[row[\'latitud\'], row[\'longitud\'], row[\'peso\']] for i


**Mapa por categoría comercial (Radio de 500 m)**

Este mapa interactivo muestra la **distribución de los comercios clasificados por categoría** dentro del área de influencia inmediata (500 metros) de Cabanna Tijuana.

Cada punto representa un establecimiento, y su color indica el **giro comercial o actividad económica**. Esta visualización permite identificar patrones de concentración, presencia de sectores dominantes y posibles áreas de saturación.


In [14]:

# ==========================================

mapa, lista_restaurantes = mapa_por_categoria(df_tijuana, "Restaurantes", coord_cabanna)

# Ver los primeros 10 restaurantes más cercanos
lista_restaurantes[["nom_estab", "distancia_m"]].head(20)


nom_estab  distancia_m
0                        SHUSHY FACTORY    70.567756
1                     RESTAURANTE GARRA    70.567756
2                           CASA DE LEO    70.567756
3                  RESTAURANT MULLIGANS    70.634698
4                                 MOCCA    70.634698
5                  EL LUQUEÑO BOTANERO.    70.634698
6                         SUSHI FACTORY    98.910130
7                LA BODEGA 8 DE LA BAJA   108.301566
8                     LORENZA ALIMENTOS   109.556026
9                       PUB DE LA CHAPU   114.433489
10                               TABULE   114.433489
11  RESTAURANT COMIDA CHINA LA MARIPOSA   146.308803
12                   PAN E VINO OSTERIA   154.067812
13              DA SALVATORE RISTORANTE   154.067812
14               RESTAURAN BAR DIMITRIS   154.067812
15  EL CAMPERO PARRILLA ARGENTINA & BAR   170.011742
16                              TACONGO   175.305263
17                   RESTAURANTE MARIEE   247.088525
18                 RESTAURANT GRAN CHEF   259.361184
19                            BAJA POKE   260.004742

In [15]:
# Mostrar mapa
mapa



**Mapa de Todos los Comercios en el Radio de 500 m**

El siguiente mapa muestra la ubicación de **todos los comercios identificados** dentro del radio de 500 metros alrededor de la sucursal Cabanna Tijuana.

**Total de comercios detectados:** 581

Esta visualización permite observar la **densidad comercial general**, independientemente de la categoría, y sirve como base para comparar con otros análisis temáticos o sectoriales.




In [16]:


# Crear mapa centrado en Cabanna
mapa = folium.Map(location=coord_cabanna, zoom_start=17)

# Añadir punto de Cabanna
folium.Marker(
    coord_cabanna, 
    tooltip="Cabanna Tijuana", 
    icon=folium.Icon(color="red")
).add_to(mapa)

# Añadir buffer de 500 metros
folium.Circle(
    coord_cabanna, 
    radius=500, 
    color='blue', 
    fill=True, 
    fill_opacity=0.1
).add_to(mapa)

# Añadir comercios cercanos de df_tijuana
for _, row in df_tijuana.iterrows():
    folium.Marker(
        location=[row['latitud'], row['longitud']],
        tooltip=row['nom_estab'],
        icon=folium.Icon(color="gray", icon="briefcase", prefix="fa")
    ).add_to(mapa)


# Mostrar mapa
mapa




**Score de competencia ponderado**

El objetivo de este indicador es reflejar la **presión competitiva** que enfrenta la sucursal Cabanna Tijuana, tomando en cuenta tanto el **número de negocios cercanos** como su **nivel de similitud o sustitución** con la oferta de Cabanna.

**Lógica de cálculo**

Cada categoría comercial dentro del radio de 500 m recibe un **peso relativo** según su grado de competencia directa con el giro de Cabanna. Los pesos asignados reflejan el nivel de amenaza competitiva que representa cada tipo de negocio.

| Categoría                         | Peso asignado |
|----------------------------------|----------------|
| Restaurantes                     | 1.00           |
| Cafeterías y neverías           | 0.80           |
| Bares y cantinas                | 0.90           |
| Taquerías y torterías           | 0.70           |
| Restaurantes autoservicio       | 0.60           |
| Inmobiliarias, ópticas, bancos  | 0.00           |

Estos pesos serán utilizados para calcular un **índice ponderado**, donde se multiplica el número de negocios por su respectivo peso. El resultado será un score entre 0 y el total máximo ponderado posible, que nos permitirá comparar zonas con diferente composición comercial.




In [17]:
# ================================================
# Cálculo del Score de Competencia Ponderado (Tijuana)
# ================================================

# ------------------------------
# Paso 1: Definir los pesos por categoría
# ------------------------------

# Se define un diccionario que asigna un peso a cada categoría de comercio
# según su nivel de competencia directa con el giro de Cabanna.
# Categorías no listadas tendrán un peso por defecto de 0.
pesos_categoria = {
    "Restaurantes": 1.00,
    "Bares y cantinas": 0.90,
    "Cafeterías y neverías": 0.80,
    "Taquerías y torterías": 0.70,
    "Restaurantes autoservicio": 0.60,
    "Salones de belleza": 0.00,
    "Despachos jurídicos": 0.00,
    "Bancos": 0.00,
    "Consultorios dentales": 0.00,
    "Contadores y auditores": 0.00
}

# ------------------------------
# Paso 2: Asignar pesos al DataFrame
# ------------------------------

# Se crea una nueva columna 'peso_competencia' en `df_tijuana`
# mapeando la categoría comercial ('nombre_act') con el peso correspondiente.
# Si la categoría no está en el diccionario, se asigna un peso de 0.
df_tijuana["peso_competencia"] = df_tijuana["nombre_act"].map(pesos_categoria).fillna(0)

# ------------------------------
# Paso 3: Calcular el Score de Competencia Ponderado
# ------------------------------

# El score final se obtiene sumando los pesos individuales asignados a cada comercio
score_competencia_ponderado = df_tijuana["peso_competencia"].sum()

# ------------------------------
# (Opcional) Guardar el resultado en la base de sucursales
# ------------------------------

# Se asigna el score calculado a la fila correspondiente a la sucursal Tijuana
datos_sucursales.loc[
    datos_sucursales["nombre_sucursal"] == "Tijuana",
    "score_competencia_ponderado"
] = score_competencia_ponderado

# Mostrar resultado final
print(f"Score de competencia ponderado para Cabanna Tijuana: {score_competencia_ponderado:.2f}")


Score de competencia ponderado para Cabanna Tijuana: 89.10




###  Interpretación Técnica del Score de Competencia: **89.10**

Este score representa la **suma de los pesos asignados** a cada negocio cercano a Cabanna Tijuana dentro del radio de 500 metros, según su nivel de competencia en la zona por categoria.

Cada establecimiento recibió un valor entre 0 y 1, dependiendo de qué tan directamente compite con el giro de Cabanna:

| Categoría                | Peso asignado |
|--------------------------|----------------|
| Restaurante              | 1.00           |
| Bar o cantina            | 0.90           |
| Cafetería o nevería      | 0.80           |
| Taquería o tortería      | 0.70           |
| Autoservicio             | 0.60           |
| Otros (bancos, abogados) | 0.00           |



###  ¿Qué significa un score de **89.10**?

Esto implica que la **presión competitiva** en la zona equivale a tener **89 negocios relevantes** compitiendo directamente por categoria.

> No es un conteo bruto de negocios.  
> Es un **conteo ajustado por relevancia competitiva**.

Si todos los **581 comercios** cercanos fueran restaurantes (peso = 1), el score máximo posible sería **581.00**.

Entonces:

$$\frac{89.10}{581} \approx 15.33\%$$

Cabanna enfrenta aproximadamente un **15.3 % de competencia efectiva** en su zona de influencia inmediata.




### Clasificación de la zona urbana a partir del entorno comercial

**Objetivo**
Determinar el **tipo de zona urbana** (comercial, residencial, mixta, turística, etc.) en la que se encuentra un comercio, utilizando como base la composición de actividades económicas presentes en su entorno cercano.

**Metodología General**

1. **Obtener la ubicación geográfica del comercio**
   - Se parte de las coordenadas de latitud y longitud de la sucursal.
   

2. **Delimitar el área de influencia**
   - Se genera un **buffer geográfico** (área circular) alrededor del punto, con un radio de 500 metros.
   - Este radio representa el entorno urbano inmediato que influye en la actividad del comercio.

3. **Extraer actividades económicas en el buffer**
   - Se utilizan fuentes como:
     - **DENUE (INEGI)**  para obtener negocios cercanos por tipo.
   - Para cada establecimiento cercano se identifica su **giro o categoría económica**.

4. **Normalizar y clasificar las actividades**
   - Se usa un **diccionario de categorías** para traducir las actividades económicas específicas a una categoría más general y manejable.
   - Ejemplo:
     - `"Comercio al por menor de ropa"` → `"Tiendas de ropa"`
     - `"Consultorios de medicina general"` → `"Médicos generales"`

5. **Agrupar las categorías en macrogrupos funcionales**
   Las categorías generales se agrupan en los siguientes **6 macrogrupos**:

   | Macrogrupo                  | Ejemplos de categorías incluidas |
   |-----------------------------|-----------------------------------|
   | Comercial                 | Restaurantes, tiendas, supermercados, cafeterías, ópticas, etc. |
   | Servicios profesionales   | Consultorios médicos, abogados, contadores, consultores, sofomes |
   | Residencial              | Construcción de vivienda, renta de departamentos |
   | Industrial / Técnica     | Plantas industriales, construcción técnica, maquinaria |
   | Turístico / Entretenimiento | Hoteles, bares, cines, marisquerías |
   | Institucional / Educación | Escuelas, asociaciones civiles, religiosas |

6. **Calcular proporciones por macrogrupo**
   - Se cuentan cuántos negocios hay de cada macrogrupo dentro del buffer.
   - Se calcula el porcentaje que representa cada macrogrupo respecto al total.

7. **Clasificar el tipo de zona**
   - Se aplican reglas basadas en proporciones para determinar el uso dominante del suelo en la zona.

## Reglas de clasificación de zonas urbanas

| Tipo de Zona                     | Reglas aplicadas según proporción de actividades |
|----------------------------------|---------------------------------------------------|
| **Zona Comercial**               | ≥ 60% de negocios del grupo `Comercial` |
| **Zona de Servicios Profesionales** | ≥ 50% `Servicios profesionales` y < 30% `Comercial` |
| **Zona Mixta**                   | 30–60% `Comercial`, combinada con ≥ 20% de al menos otro grupo |
| **Zona Turística / Entretenimiento** | ≥ 40% del grupo `Turístico / Entretenimiento` |
| **Zona Institucional / Educativa** | ≥ 40% del grupo `Institucional / Educación` |
| **Zona Industrial / Técnica**    | ≥ 30% del grupo `Industrial / Técnica` |
| **Zona Predominantemente Residencial** | < 30% de cualquier grupo y predominancia de vivienda u oficinas sin actividad comercial |



In [18]:

# ------------------------------
# 1. Cargar tu DataFrame de negocios cercanos
# ------------------------------
# Se asume que ya tienes cargado tu DataFrame con negocios en un radio (ej. 500 m)
# Ejemplo: df_tijuana = pd.read_csv('negocios_tijuana_buffer.csv')

# ------------------------------
# 2. Diccionario de mapeo a macrogrupos
# ------------------------------
macrogrupos = {
    "comercial": [
        "Restaurantes", "Taquerías y torterías", "Comida rápida americana", "Comida rápida para llevar",
        "Supermercados", "Minisúpers", "Abarrotes", "Tiendas de ropa", "Tiendas de cosméticos", 
        "Ópticas", "Licorerías", "Tiendas de celulares", "Papelerías", "Mueblerías"
    ],
    "servicios_profesionales": [
        "Médicos generales", "Médicos especialistas", "Consultorios dentales", "Psicólogos",
        "Consultoría administrativa", "Consultoría técnica", "Contadores y auditores", 
        "Bufetes jurídicos", "Notarías", "Agentes de seguros", "Sofomes", "Call centers"
    ],
    "residencial": [
        "Construcción vivienda unifamiliar", "Construcción vivienda multifamiliar", "Renta temporal vivienda"
    ],
    "industrial": [
        "Construcción industrial", "Instalaciones eléctricas", "Renta de maquinaria", "Elaboración de vino"
    ],
    "turistico": [
        "Hoteles", "Bares y cantinas", "Cafeterías y neverías", "Cines", 
        "Marisquerías", "Restaurantes autoservicio", "Renta de salones", "Catering"
    ],
    "institucional": [
        "Escuelas de arte", "Asociaciones religiosas", "Asociaciones civiles", 
        "Arquitectura", "Empleo temporal"
    ]
}

# ------------------------------
# 3. Contar categorías por macrogrupo
# ------------------------------
def contar_macrogrupos(df, columna_categoria):
    conteo = {k: 0 for k in macrogrupos}
    total = 0

    for _, row in df.iterrows():
        categoria = row[columna_categoria]
        total += 1
        for grupo, lista in macrogrupos.items():
            if categoria in lista:
                conteo[grupo] += 1
                break  # solo pertenece a un grupo

    porcentajes = {k: round((v / total) * 100, 2) if total > 0 else 0 for k, v in conteo.items()}
    return conteo, porcentajes

# ------------------------------
# 4. Clasificar tipo de zona según reglas
# ------------------------------
def clasificar_zona(porcentajes):
    c = porcentajes['comercial']
    s = porcentajes['servicios_profesionales']
    t = porcentajes['turistico']
    i = porcentajes['industrial']
    inst = porcentajes['institucional']

    if c >= 60:
        return "Zona Comercial"
    elif t >= 40:
        return "Zona Turística / Entretenimiento"
    elif s >= 50 and c < 30:
        return "Zona de Servicios Profesionales"
    elif i >= 30:
        return "Zona Industrial / Técnica"
    elif inst >= 40:
        return "Zona Institucional / Educativa"
    elif 30 <= c < 60:
        return "Zona Mixta"
    else:
        return "Zona Predominantemente Residencial"

# ------------------------------
# 5. Aplicar al DataFrame
# ------------------------------
# Usar columna 'Principal Actividad Economica' o la columna renombrada que tú elegiste
conteo, porcentajes = contar_macrogrupos(df_tijuana, "nombre_act")

zona_clasificada = clasificar_zona(porcentajes)

# ------------------------------
# 6. Imprimir resultados
# ------------------------------
print("📍 Zona clasificada:", zona_clasificada)
print("📊 Porcentajes por macrogrupo:")
for grupo, porcentaje in porcentajes.items():
    print(f"  - {grupo}: {porcentaje}%")


📍 Zona clasificada: Zona Predominantemente Residencial
📊 Porcentajes por macrogrupo:
  - comercial: 14.63%
  - servicios_profesionales: 14.29%
  - residencial: 1.55%
  - industrial: 1.03%
  - turistico: 10.15%
  - institucional: 1.89%


---

### Análisis detallado: sucursal Cabanna Mexicali

In [19]:
# ==============================
# Análisis geoespacial de competencia en Mexicali
# ==============================

# ------------------------------
# 1. Obtener coordenadas de la sucursal Cabanna en Mexicali
# ------------------------------

# Filtra el DataFrame de sucursales para encontrar la sucursal de Cabanna ubicada en TiMexicalijuana
# Se usa `.iloc[0]` porque se espera un solo resultado
sucursal_mexicali = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Mexicali"].iloc[0]

# Se extraen las coordenadas (latitud, longitud) de la sucursal
coord_cabanna_mexicali = (sucursal_mexicali["latitud"], sucursal_mexicali["longitud"])

# ------------------------------
# 2. Calcular distancia geodésica desde cada comercio a Cabanna Mexicali
# ------------------------------

# Se calcula la distancia entre cada comercio en Baja California y la sucursal Cabanna en Mexicali
# Se usa geodesic (que toma en cuenta la curvatura de la tierra) para mayor precisión
df_baja_california["distancia_m"] = df_baja_california.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_mexicali).meters,
    axis=1
)

# Se ordenan los comercios por distancia ascendente (los más cercanos primero)
df_baja_california.sort_values(by="distancia_m", inplace=True)

# ------------------------------
# 3. Filtrar únicamente los comercios del municipio de Mexicali
# ------------------------------

df_mexicali = df_baja_california[df_baja_california['municipio'] == 'Mexicali'].copy()

# Se eliminan columnas que ya no se necesitan para el análisis final
df_mexicali.drop(columns=['Código','codigo_act'], inplace=True)

# ------------------------------
# 4. Filtrar comercios dentro de un radio de 500 metros de Cabanna
# ------------------------------

df_mexicali_filtrado_500 = df_mexicali[df_mexicali["distancia_m"] <= 500]

# ------------------------------
# 5. Eliminar duplicados geográficos (comercios muy cercanos con misma lat/lon)
# ------------------------------

# Se asume que `eliminar_duplicados_geograficos` es una función definida previamente
df_mexicali = eliminar_duplicados_geograficos(df_mexicali_filtrado_500)

# Se vuelve a ordenar por distancia tras eliminar duplicados
df_mexicali.sort_values(by="distancia_m", inplace=True)

# ------------------------------
# 6. Exportar resultado limpio a CSV
# ------------------------------

df_mexicali.to_csv("../data/denue_mexicali_data.csv", index=False)

# ------------------------------
# 7. Agrupar nombre de actividad económica por categorías simplificadas
# ------------------------------

# Reemplaza los nombres originales por categorías más agregadas usando un diccionario
# `diccionario_categorias` debe estar definido previamente como {'nombre original': 'categoría simple'}
df_mexicali["nombre_act"] = df_mexicali["nombre_act"].replace(diccionario_categorias)

# Mostrar los primeros 5 registros como vista previa
#df_mexicali.head(5)

### 1. Densidad de negocios por metro cuadrado

In [20]:
# ==============================================
# Cálculo de densidad de competencia alrededor de Cabanna Mexicali
# ==============================================

# ------------------------------
# 1. Calcular el área del buffer circular de 500 metros
# ------------------------------

# Se utiliza la fórmula del área de un círculo: A = π * r²
# En este caso, r = 500 metros
area_m2 = np.pi * (500**2)  # Resultado ≈ 785,398 m²

# ------------------------------
# 2. Contar número de comercios dentro del buffer
# ------------------------------

# Se toma el número de filas del DataFrame filtrado (df_mexicali),
# que ya contiene solo los comercios dentro del radio de 500 m
num_comercios = df_mexicali.shape[0]

# ------------------------------
# 3. Calcular densidad de competencia (comercios por m²)
# ------------------------------

# Se divide el número de comercios entre el área del buffer
# El resultado es un valor de densidad: cuántos comercios hay por metro cuadrado
densidad_competencia = num_comercios / area_m2

# ------------------------------
# 4. Asignar el valor de densidad a la sucursal Mexicali
# ------------------------------

# Se guarda este valor en una nueva columna en el DataFrame `datos_sucursales`,
# específicamente para la fila correspondiente a la sucursal "Mexicali"
datos_sucursales.loc[
    datos_sucursales["nombre_sucursal"] == "Mexicali",
    "densidad_competencia_500m"
] = densidad_competencia

densidad_competencia

0.00030939720937064457


**Resultado de la densidad de negocios**

La **densidad de negocios** es de:

$$0.00030939720937064457\ \text{comercios/m}^2$$

Lo que equivale aproximadamente a:

$$309.397 \ \text{comercios/km}^2$$

Este valor representa la **cantidad de negocios** dentro del radio de 500 metros (área de influencia inmediata) alrededor de la sucursal Cabanna Mexicali.

## 2 Conteo de comercios por categoría (Actividad)

In [21]:
# ===============================================
# Conteo de comercios por categoría (nombre_act)
# ===============================================

# ------------------------------
# 1. Contar frecuencia de cada categoría
# ------------------------------

# Se cuenta cuántos comercios hay por categoría de actividad dentro del radio de 500m
# `nombre_act` contiene el giro comercial como "cafetería", "restaurante", "bar", etc.
conteo_por_categoria_mexicali = df_mexicali["nombre_act"].value_counts().reset_index()

# Se renombran las columnas para mayor claridad
conteo_por_categoria_mexicali.columns = ["categoria", "conteo"]

# ------------------------------
# 2. (Opcional) Exportar a CSV para usar en reportes externos
# ------------------------------

# Si se desea guardar el conteo para documentación o análisis adicional:
# conteo_por_categoria_mexicali.to_csv("../data/conteo_categorias_500m_Mexicali.csv", index=False)

# ------------------------------
# 3. Mostrar resultados clave
# ------------------------------

# Mostrar el número total de comercios en el área de análisis
print("Número total de comercios en un radio de 500m de Cabanna:", conteo_por_categoria_mexicali['conteo'].sum())

# Mostrar las 20 categorías más frecuentes
conteo_por_categoria_mexicali.head(20)


Número total de comercios en un radio de 500m de Cabanna: 243


categoria  conteo
0                                        Restaurantes      26
1                                     Tiendas de ropa      25
2                                              Bancos      21
3                                  Salones de belleza      18
4                           Restaurantes autoservicio      14
5                               Cafeterías y neverías      13
6                                             Ópticas       9
7                    Comercio al por menor de calzado       7
8                                Tiendas de celulares       7
9   Comercio al por menor de bisutería y accesorio...       6
10                              Tiendas de cosméticos       4
11  Comercio al por menor de artículos de joyería ...       4
12                              Taquerías y torterías       4
13                              Consultorios dentales       4
14                                         Mueblerías       3
15                                      Inmobiliarias       3
16                                              Cines       3
17                                          Gimnasios       3
18                            Comida rápida americana       3
19                          Comida rápida para llevar       2

In [22]:

px.bar(
    conteo_por_categoria_mexicali.head(10),
    x="conteo", y="categoria",
    orientation="h",
    title="Top 10 categorías comerciales en radio de 500m",
    labels={"conteo": "Número de comercios", "categoria": "Categoría"}
)

## Validación visual: mapa de competencia directa

Se presenta a continuación un **mapa interactivo generado con Folium**, que permite visualizar la **competencia directa** alrededor de la sucursal Cabanna Mexicali.

Este mapa muestra los comercios identificados dentro de un radio de **500 metros**, facilitando la validación visual de su ubicación, densidad y proximidad relativa a la sucursal.

In [23]:

# Filtrar competencia en Mexicali
competencia_mexicali = datos_competencia[datos_competencia["ciudad"] == "Mexicali"].copy()

import folium
from geopy.distance import geodesic

# Crear mapa centrado en Cabanna
mapa = folium.Map(location=coord_cabanna_mexicali, zoom_start=17)

# Añadir punto de Cabanna
folium.Marker(
    coord_cabanna_mexicali, 
    tooltip="Cabanna Mexicali", 
    icon=folium.Icon(color="red")
).add_to(mapa)

# Añadir buffer de 500 metros
folium.Circle(
    coord_cabanna_mexicali, 
    radius=500, 
    color='blue', 
    fill=True, 
    fill_opacity=0.1
).add_to(mapa)



# Añadir competencia directa en verde y dibujar líneas con distancia
for _, row in competencia_mexicali.iterrows():
    coord_competidor = (row['latitud'], row['longitud'])
    distancia_m = geodesic(coord_cabanna_mexicali, coord_competidor).meters
    etiqueta = f"{row['restaurante']} ({round(distancia_m,1)} m)"

    # Marcar competidor en verde
    folium.Marker(
        location=coord_competidor,
        tooltip=etiqueta,
        icon=folium.Icon(color="green", icon="cutlery", prefix="fa")
    ).add_to(mapa)

    # Dibujar línea
    folium.PolyLine(
        locations=[coord_cabanna_mexicali, coord_competidor],
        color="green",
        weight=2,
        opacity=0.7
    ).add_to(mapa)

# Mostrar mapa
mapa

**Mapa por categoría comercial (Radio de 500 m)**

Este mapa interactivo muestra la **distribución de los comercios clasificados por categoría** dentro del área de influencia inmediata (500 metros) de Cabanna Mexicali.

Cada punto representa un establecimiento, y su color indica el **giro comercial o actividad económica**. Esta visualización permite identificar patrones de concentración, presencia de sectores dominantes y posibles áreas de saturación.

In [24]:

mapa, lista_restaurantes = mapa_por_categoria(df_mexicali, "Restaurantes", coord_cabanna_mexicali)

# Ver los primeros 10 restaurantes más cercanos
lista_restaurantes[["nom_estab", "distancia_m"]].head(20)

nom_estab  distancia_m
0              HOLY COW    25.516185
1            ALMA VERDE   123.876566
2             DEVORALIA   123.876566
3                ARDENA   123.876566
4               MARAKAI   123.876566
5              HOLY COW   124.281379
6                  IHOP   124.281379
7   CABANNA RESTAURANTE   124.281379
8                TAVOLA   124.281379
9           SABROSISIMA   124.281379
10              MESTIZO   124.281379
11        ASIAN WOK BOX   124.281379
12          BAJA BRUNCH   124.281379
13    VINOS TRAS LUPITA   124.281379
14        TACOS CHICALI   124.281379
15                LOLAS   187.299670
16            WRAPISIMO   206.625934
17      ORIGAME EXPRESS   206.625934
18             MOCHOMOS   206.625934
19           HAPPY SALD   222.948754

In [25]:
# Mostrar mapa
mapa


**Score de competencia ponderado**

In [26]:

# ------------------------------
# Paso 2: Asignar pesos al DataFrame
# ------------------------------

# Se crea una nueva columna 'peso_competencia' en `df_mexicali`
# mapeando la categoría comercial ('nombre_act') con el peso correspondiente.
# Si la categoría no está en el diccionario, se asigna un peso de 0.
df_mexicali["peso_competencia"] = df_mexicali["nombre_act"].map(pesos_categoria).fillna(0)

# ------------------------------
# Paso 3: Calcular el Score de Competencia Ponderado
# ------------------------------

# El score final se obtiene sumando los pesos individuales asignados a cada comercio
score_competencia_ponderado = df_mexicali["peso_competencia"].sum()

# ------------------------------
# (Opcional) Guardar el resultado en la base de sucursales
# ------------------------------

# Se asigna el score calculado a la fila correspondiente a la sucursal Mexicali
datos_sucursales.loc[
    datos_sucursales["nombre_sucursal"] == "Mexicali",
    "score_competencia_ponderado"
] = score_competencia_ponderado

# Mostrar resultado final
print(f"Score de competencia ponderado para Cabanna Mexicali: {score_competencia_ponderado:.2f}")


Score de competencia ponderado para Cabanna Mexicali: 49.40


### Clasificación de la zona urbana a partir del entorno comercial

# Sinaloa-Culiacán


In [27]:
# Datos de los comercios en Baja California DENUE   
df_sinaloa= pd.read_csv("../Sinaloa_comercios.csv", encoding="latin1")
df_sinaloa = df_sinaloa[[ 'entidad','municipio','nom_estab','codigo_act', 'nombre_act','per_ocu','tipoCenCom','latitud', 'longitud']].copy()

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
df_sinaloa["codigo_act"] = df_sinaloa["codigo_act"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
df_sinaloa = df_sinaloa.merge(scian,left_on="codigo_act", right_on="Código", how = "left")

# Se renombra la columna a utilizar
df_sinaloa = df_sinaloa.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = df_sinaloa.pop("Principal Actividad Economica")
df_sinaloa.insert(5,"Principal Actividad Economica", col_a)
# Obtener sucursal Cabanna en Tijuana
sucursal_culiacan = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Culiacán"].iloc[0]
coord_cabanna_culiacan= (sucursal_culiacan["latitud"], sucursal_culiacan["longitud"])

# Calcular distancia de la sucursal Cabanna a los comercios en Culiacán
df_sinaloa["distancia_m"] = df_sinaloa.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_culiacan).meters,
    axis=1
)
    
df_sinaloa.sort_values(by="distancia_m", inplace=True)
df_culiacan = df_sinaloa[df_sinaloa['municipio'] == 'Culiacán'].copy()
df_culiacan.drop(columns=['Código','codigo_act'], inplace=True)
df_culiacan_filtrado_500 = df_culiacan[df_culiacan["distancia_m"] <= 500]
df_culiacan_filtrado_500.to_csv("../denue_culiacan_data.csv", index=False)
df_culiacan_filtrado_500.head(5)



FileNotFoundError: [Errno 2] No such file or directory: '../Sinaloa_comercios.csv'

In [ ]:
# Filtrar competencia en Tijuana
competencia_culiacan = datos_competencia[datos_competencia["ciudad"] == "Culiacán"].copy()
competencia_culiacan

# Jalisco - Guadalajara Av México

In [ ]:
# Datos de los comercios en Baja California DENUE   
df_jalisco= pd.read_csv("../Jalisco_comercios.csv", encoding="latin1")
df_jalisco = df_jalisco[[ 'entidad','municipio','nom_estab','codigo_act', 'nombre_act','per_ocu','tipoCenCom','latitud', 'longitud']].copy()

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
df_jalisco["codigo_act"] = df_jalisco["codigo_act"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
df_jalisco = df_jalisco.merge(scian,left_on="codigo_act", right_on="Código", how = "left")

# Se renombra la columna a utilizar
df_jalisco = df_jalisco.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = df_jalisco.pop("Principal Actividad Economica")
df_jalisco.insert(5,"Principal Actividad Economica", col_a)

# Obtener sucursal Cabanna en Guadalajara Av México
sucursal_guadalajara_méxico = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Guadalajara Av México"].iloc[0]
coord_cabanna_guadalajara_méxico= (sucursal_guadalajara_méxico["latitud"], sucursal_guadalajara_méxico["longitud"])

# Calcular distancia de la sucursal Cabanna a los comercios en Guadalajara Av México
df_jalisco["distancia_m"] = df_jalisco.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_guadalajara_méxico).meters,
    axis=1
)

df_jalisco.sort_values(by="distancia_m", inplace=True)
df_guadalajara_méxico = df_jalisco[df_jalisco['municipio'] == 'Guadalajara'].copy()
df_guadalajara_méxico.drop(columns=['Código','codigo_act'], inplace=True)
df_guadalajara_méxico_filtrado_500 = df_guadalajara_méxico[df_guadalajara_méxico["distancia_m"] <= 500]
df_guadalajara_méxico_filtrado_500.to_csv("../denue_guadalajara_av_mexico_data.csv", index=False)
df_guadalajara_méxico_filtrado_500.head(5)


# Jalisco - Guadalajara Sur Gurmeteria

In [ ]:
# Obtener sucursal Cabanna en Guadalajara Gurmeteria
sucursal_guadalajara_sur = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Guadalajara Gpurmeteria"].iloc[0]
coord_cabanna_guadalajara_sur= (sucursal_guadalajara_sur["latitud"], sucursal_guadalajara_sur["longitud"])

# Calcular distancia de la sucursal Cabanna a los comercios en Guadalajara Av México
df_jalisco["distancia_m"] = df_jalisco.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_guadalajara_sur).meters,
    axis=1
)

df_jalisco.sort_values(by="distancia_m", inplace=True)
df_guadalajara_sur= df_jalisco[df_jalisco['municipio'] == 'Tlajomulco de Zúñiga'].copy()
df_guadalajara_sur.drop(columns=['Código','codigo_act'], inplace=True)
df_guadalajara_sur_filtrado_500 = df_guadalajara_sur[df_guadalajara_sur["distancia_m"] <= 500]
df_guadalajara_sur_filtrado_500.to_csv("../denue_guadalajara_sur_data.csv", index=False)
df_guadalajara_sur_filtrado_500.head(5)

In [ ]:
# Filtrar competencia en Guadalajara
competencia_Guadalajara = datos_competencia[datos_competencia["ciudad"] == "Guadalajara"].copy()
competencia_Guadalajara

# CDMX - Polanco

In [ ]:
# Datos de los comercios en Baja California DENUE   
df_cdmx= pd.read_csv("../CDMX_comercios.csv", encoding="latin1")
df_cdmx = df_cdmx[[ 'entidad','municipio','nom_estab','codigo_act', 'nombre_act','per_ocu','tipoCenCom','latitud', 'longitud']].copy()

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
df_cdmx["codigo_act"] = df_cdmx["codigo_act"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
df_cdmx = df_cdmx.merge(scian,left_on="codigo_act", right_on="Código", how = "left")

# Se renombra la columna a utilizar
df_cdmx = df_cdmx.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = df_cdmx.pop("Principal Actividad Economica")
df_cdmx.insert(5,"Principal Actividad Economica", col_a)

# Obtener sucursal Cabanna en Guadalajara Av México
sucursal_cdmx = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Polanco"].iloc[0]
coord_cabanna_cdmx= (sucursal_cdmx["latitud"], sucursal_cdmx["longitud"])

# Calcular distancia de la sucursal Cabanna a los comercios en Guadalajara Av México
df_cdmx["distancia_m"] = df_cdmx.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_cdmx).meters,
    axis=1
)

df_cdmx.sort_values(by="distancia_m", inplace=True)
df_cdmx
df_cdmx= df_cdmx[df_cdmx['municipio'] == 'Miguel Hidalgo'].copy()
df_cdmx.drop(columns=['Código','codigo_act'], inplace=True)
df_cdmx_filtrado_500 = df_cdmx[df_cdmx["distancia_m"] <= 500]
df_cdmx_filtrado_500.to_csv("../denue_cdmx_data.csv", index=False)
df_cdmx_filtrado_500.head(5)


In [ ]:
# Filtrar competencia en CDMX
competencia_cdmx= datos_competencia[datos_competencia["ciudad"] == "CDMX"].copy()
competencia_cdmx

# Nuevo León - Metropolitan

In [ ]:


# Datos de los comercios en Nuevo León DENUE   
df_nl= pd.read_csv("../Nuevo_Leon_comercios.csv", encoding="latin1")
df_nl = df_nl[[ 'entidad','municipio','nom_estab','codigo_act', 'nombre_act','per_ocu','tipoCenCom','latitud', 'longitud']].copy()

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
df_nl["codigo_act"] = df_nl["codigo_act"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
df_nl = df_nl.merge(scian,left_on="codigo_act", right_on="Código", how = "left")

# Se renombra la columna a utilizar
df_nl = df_nl.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = df_nl.pop("Principal Actividad Economica")
df_nl.insert(5,"Principal Actividad Economica", col_a)

# Obtener sucursal Cabanna en Guadalajara Av México
sucursal_nl = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Metropolitan"].iloc[0]
coord_cabanna_nl= (sucursal_nl["latitud"], sucursal_nl["longitud"])

# Calcular distancia de la sucursal Cabanna a los comercios en Guadalajara Av México
df_nl["distancia_m"] = df_nl.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_nl).meters,
    axis=1
)

df_nl.sort_values(by="distancia_m", inplace=True)
df_nl
df_nl= df_nl[df_nl['municipio'] == 'San Pedro Garza García'].copy()
df_nl.drop(columns=['Código','codigo_act'], inplace=True)
df_nl_filtrado_500 = df_nl[df_nl["distancia_m"] <= 500]
df_nl_filtrado_500.to_csv("../denue_metropolitan_data.csv", index=False)
df_nl_filtrado_500.head(5)

In [ ]:
# Filtrar competencia en Nuevo León
competencia_nl = datos_competencia[datos_competencia["ciudad"] == "Monterrey"].copy()
competencia_nl

# Puebla - Puebla

In [ ]:

# Datos de los comercios en Nuevo León DENUE   
df_puebla= pd.read_csv("../Puebla_comercios.csv", encoding="latin1")
df_puebla = df_puebla[[ 'entidad','municipio','nom_estab','codigo_act', 'nombre_act','per_ocu','tipoCenCom','latitud', 'longitud']].copy()

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
df_puebla["codigo_act"] = df_puebla["codigo_act"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
df_puebla = df_puebla.merge(scian,left_on="codigo_act", right_on="Código", how = "left")

# Se renombra la columna a utilizar
df_puebla = df_puebla.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = df_puebla.pop("Principal Actividad Economica")
df_puebla.insert(5,"Principal Actividad Economica", col_a)

# Obtener sucursal Cabanna en Guadalajara Av México
sucursal_puebla = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Puebla"].iloc[0]
coord_cabanna_puebla= (sucursal_puebla["latitud"], sucursal_puebla["longitud"])

# Calcular distancia de la sucursal Cabanna a los comercios en Guadalajara Av México
df_puebla["distancia_m"] = df_puebla.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_puebla).meters,
    axis=1
)

df_puebla.sort_values(by="distancia_m", inplace=True)
df_puebla= df_puebla[df_puebla['municipio'] == 'Puebla'].copy()
df_puebla.drop(columns=['Código','codigo_act'], inplace=True)
df_puebla_filtrado_500 = df_puebla[df_puebla["distancia_m"] <= 500]
df_puebla_filtrado_500.to_csv("../denue_puebla_data.csv", index=False)
df_puebla_filtrado_500.head(5)

# Chihuahua - Juarez

In [ ]:

# Datos de los comercios en Nuevo León DENUE   
df_juarez= pd.read_csv("../Chihuahua_comercios.csv", encoding="latin1")
df_juarez = df_juarez[[ 'entidad','municipio','nom_estab','codigo_act', 'nombre_act','per_ocu','tipoCenCom','latitud', 'longitud']].copy()

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
df_juarez["codigo_act"] = df_juarez["codigo_act"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
df_juarez = df_juarez.merge(scian,left_on="codigo_act", right_on="Código", how = "left")

# Se renombra la columna a utilizar
df_juarez = df_juarez.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = df_juarez.pop("Principal Actividad Economica")
df_juarez.insert(5,"Principal Actividad Economica", col_a)

# Obtener sucursal Cabanna en Guadalajara Av México
sucursal_juarez = datos_sucursales[datos_sucursales["nombre_sucursal"] == "Ciudad Juárez"].iloc[0]
coord_cabanna_juarez= (sucursal_juarez["latitud"], sucursal_juarez["longitud"])

# Calcular distancia de la sucursal Cabanna a los comercios en Guadalajara Av México
df_juarez["distancia_m"] = df_juarez.apply(
    lambda row: geodesic((row['latitud'], row['longitud']), coord_cabanna_juarez).meters,
    axis=1
)

df_juarez.sort_values(by="distancia_m", inplace=True)
df_juarez= df_juarez[df_juarez['municipio'] == 'Juárez'].copy()
df_juarez.drop(columns=['Código','codigo_act'], inplace=True)
df_juarez_filtrado_500 = df_juarez[df_juarez["distancia_m"] <= 500]
df_juarez_filtrado_500.to_csv("../denue_juarez_data.csv", index=False)
df_juarez_filtrado_500.head(5)